In [1]:
import os
import re
import pandas as pd

# Data preprocessing

Extract experiment settings and No. of violations

## get worker data

Function: getWorkerData

Inputs:

    folderDir: directory containing all design logs

    outputPath: output csv file name

Outputs:

    data: a pandas.DataFrame containing all worker DRC values with the following columns

    design iteration worker_pos_1 worker_pos_2 time prev_drc curr_drc

if folderDir exists:

    data, design = init()
    
    for each design:

        detect("Start detail routing")
        
        while not detect("Complete detail routing"):

            iter = detect("Start %dth optimization iteration")

            tmpData = init()

            while not detect("Completing 100\% with %d violations")

                tmp = parseWorkerData(line)

                tmpData.append(tmp)
                
            writeData(design, iter, tmpData, data)

    save(outputPath, data)

    return data

In [2]:
def getWorkerData(folderDir: str, outputPath: str, save: bool=True) -> pd.DataFrame:
    """parse worker data, save results to csv file, and return dataframe"""

    columns = ["designIndex", "design", "iter", "pos1x", "pos1y", "pos2x", "pos2y", "time", "prev_drc", "curr_drc"]
    data = pd.DataFrame([], columns=columns)
    if os.path.exists(folderDir):
        designIndex = -1
        for i, process in enumerate(os.listdir(folderDir)):
            logfileDir = os.path.join(folderDir, process)
            # debug
            designs = os.listdir(logfileDir)
            print(designs)
            for design in designs:
                logfile = os.path.join(logfileDir, design, "base", "5_3_route.log")
                # # debug
                # print(f"logfile: {logfile}")
                # check log file exists
                if not os.path.exists(logfile):
                    print(f"logfile {logfile} doesn't exist!")
                    continue
                designIndex += 1
                print(f"{designIndex} design: {process} - {design}")
                # read and parse file
                with open(logfile, 'r') as file:
                    line = file.readline()
                    iter = -1
                    while not detect("Complete detail routing", line):
                        if detect("Start \d+.. optimization iteration", line):
                            iter += 1
                            tmpData = []
                        if detect("worker", line):
                            dataline = [designIndex, process + "/" + design, iter]
                            for x in parseWorkerData(line):
                                dataline.append(x)
                            tmpData.append(dataline)
                        if detect("Completing 100% with \d+ violations.", line):
                            newData = pd.DataFrame(tmpData, columns=columns)
                            data = pd.concat([data, newData], ignore_index = True)
                        line = file.readline()
    # save data
    if save:
        outputFilename = "workerData.csv"
        if not os.path.exists(outputPath):
            print(f"Output path {outputPath} doesn't exist!")
        else:
            data.to_csv(os.path.join(outputPath, outputFilename))
        
    return data

In [3]:
def detect(pattern: str, line: str) -> bool:
    """detect whether line contains string pattern"""
    if re.search(pattern, line):
        return True
    else:
        return False

In [4]:
def parseWorkerData(line: str) -> list:
    """parse one line and extract worker data elements
    output ["pos1", "pos2", "time", "prev_drc", "curr_drc"]
    """
    _, _, _, pos1x, pos1y, pos2x, pos2y, _, time, _, prev_drc, _, curr_drc = line.split(' ')
    pos1x = float(pos1x[1:])
    pos1y = float(pos1y[:-1])
    pos2x = float(pos2x[1:])
    pos2y = float(pos2y[:-1])
    time = float(time)
    prev_drc = int(prev_drc)
    curr_drc = int(curr_drc)
    
    return [pos1x, pos1y, pos2x, pos2y, time, prev_drc, curr_drc]

In [5]:
folderDir = "../data/worker"
outputPath = "../data/dataset"
df = getWorkerData(folderDir, outputPath, save=False)

['jpeg', 'ibex', 'aes', 'gcd', 'riscv32i']
0 design: sky130hs - jpeg
1 design: sky130hs - ibex


/tmp/ipykernel_85358/2630644013.py:38: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  data = pd.concat([data, newData], ignore_index = True)


2 design: sky130hs - aes
logfile ../data/worker/sky130hs/gcd/base/5_3_route.log doesn't exist!
3 design: sky130hs - riscv32i
['uart-blocks_uart_rx', 'jpeg', 'ibex', 'uart-blocks', 'aes', 'riscv32i']
4 design: gf180 - uart-blocks_uart_rx
5 design: gf180 - jpeg
6 design: gf180 - ibex
7 design: gf180 - uart-blocks
8 design: gf180 - aes
9 design: gf180 - riscv32i
['jpeg', 'chameleon', 'microwatt', 'chameleon_hier_DFFRAM_4K', 'ibex', 'coyote_tc', 'chameleon_hier_DMC_32x16HC', 'aes', 'gcd', 'riscv32i']
10 design: sky130hd - jpeg
11 design: sky130hd - chameleon
12 design: sky130hd - microwatt
13 design: sky130hd - chameleon_hier_DFFRAM_4K
14 design: sky130hd - ibex
logfile ../data/worker/sky130hd/coyote_tc/base/5_3_route.log doesn't exist!
logfile ../data/worker/sky130hd/chameleon_hier_DMC_32x16HC/base/5_3_route.log doesn't exist!
15 design: sky130hd - aes
logfile ../data/worker/sky130hd/gcd/base/5_3_route.log doesn't exist!
16 design: sky130hd - riscv32i
['jpeg', 'swerv_wrapper', 'bp_multi',

In [6]:
df

designIndex          design iter  pos1x    pos1y  pos2x    pos2y  \
0                 0   sky130hs/jpeg    0   0.00  1008.00  50.40  1058.40   
1                 0   sky130hs/jpeg    0   0.00     0.00  50.40    50.40   
2                 0   sky130hs/jpeg    0   0.00  1108.80  50.40  1117.76   
3                 0   sky130hs/jpeg    0   0.00   907.20  50.40   957.60   
4                 0   sky130hs/jpeg    0   0.00   806.40  50.40   856.80   
...             ...             ...  ...    ...      ...    ...      ...   
1363394          38  asap7/riscv32i    4  78.84    78.84  80.00    82.62   
1363395          38  asap7/riscv32i    4  78.84    48.60  80.00    52.38   
1363396          38  asap7/riscv32i    4  63.72    86.40  67.50    90.00   
1363397          38  asap7/riscv32i    4  71.28    41.04  75.06    44.82   
1363398          38  asap7/riscv32i    4  71.28    63.72  75.06    67.50   

                 time prev_drc curr_drc  
0        1.051600e-05        1        0  
1        3.698000e-05        1        0  
2        3.006300e-05        1        0  
3        3.874400e-05        1        0  
4        3.342000e-05        1        0  
...               ...      ...      ...  
1363394  1.184000e-06        0        0  
1363395  8.740000e-07        0        0  
1363396  2.727000e-06        0        0  
1363397  3.740312e-01        3        0  
1363398  9.055929e-01        1        0  

[1363399 rows x 10 columns]

In [7]:
df.describe()

pos1x         pos1y         pos2x         pos2y          time
count  1.363399e+06  1.363399e+06  1.363399e+06  1.363399e+06  1.363399e+06
mean   1.123631e+03  1.146206e+03  1.143070e+03  1.165641e+03  2.425957e-01
std    9.998440e+02  1.022682e+03  1.001343e+03  1.024915e+03  1.514773e+00
min    0.000000e+00  0.000000e+00  1.080000e+00  1.080000e+00  1.150000e-07
25%    3.174000e+02  3.234000e+02  3.339000e+02  3.385800e+02  8.970000e-07
50%    7.791000e+02  7.791000e+02  8.004000e+02  8.022000e+02  1.387000e-06
75%    1.773300e+03  1.835400e+03  1.794000e+03  1.860600e+03  1.398500e-03
max    3.597300e+03  3.597300e+03  3.600000e+03  3.600000e+03  3.393052e+02

In [8]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1363399 entries, 0 to 1363398
Data columns (total 10 columns):
 #   Column       Non-Null Count    Dtype  
---  ------       --------------    -----  
 0   designIndex  1363399 non-null  object 
 1   design       1363399 non-null  object 
 2   iter         1363399 non-null  object 
 3   pos1x        1363399 non-null  float64
 4   pos1y        1363399 non-null  float64
 5   pos2x        1363399 non-null  float64
 6   pos2y        1363399 non-null  float64
 7   time         1363399 non-null  float64
 8   prev_drc     1363399 non-null  object 
 9   curr_drc     1363399 non-null  object 
dtypes: float64(5), object(5)
memory usage: 104.0+ MB


## data preprocessing

In [9]:
# check nan values and convert data types
for i in df.columns:
    print(f"number of nan values in {i}: {df[i].isnull().sum()}")

number of nan values in designIndex: 0
number of nan values in design: 0
number of nan values in iter: 0
number of nan values in pos1x: 0
number of nan values in pos1y: 0
number of nan values in pos2x: 0
number of nan values in pos2y: 0
number of nan values in time: 0
number of nan values in prev_drc: 0
number of nan values in curr_drc: 0


In [10]:
# convert object to int type
for i in ['designIndex', 'iter', 'prev_drc', 'curr_drc']:
    df[i] = df[i].astype('int32')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1363399 entries, 0 to 1363398
Data columns (total 10 columns):
 #   Column       Non-Null Count    Dtype  
---  ------       --------------    -----  
 0   designIndex  1363399 non-null  int32  
 1   design       1363399 non-null  object 
 2   iter         1363399 non-null  int32  
 3   pos1x        1363399 non-null  float64
 4   pos1y        1363399 non-null  float64
 5   pos2x        1363399 non-null  float64
 6   pos2y        1363399 non-null  float64
 7   time         1363399 non-null  float64
 8   prev_drc     1363399 non-null  int32  
 9   curr_drc     1363399 non-null  int32  
dtypes: float64(5), int32(4), object(1)
memory usage: 83.2+ MB


In [26]:
# # check duplicated worker
# for i in range(max(set(df['designIndex'])) + 1):
#     print(f'duplicated number of workers for design {i}: {df[df['designIndex']==i].iloc[:, :7].duplicated().values.sum()}')

SyntaxError: f-string: unmatched '[' (2448384863.py, line 3)

In [27]:
# save data
outputPath = "../data/dataset"
outputFilename = "workerData.csv"
if not os.path.exists(outputPath):
    print(f"Output path {outputPath} doesn't exist!")
else:
    df.to_csv(os.path.join(outputPath, outputFilename), index=False)

## get statistical data for each iteration

In [28]:
outputPath = "../data/dataset"
outputFilename = "workerData.csv"
df = pd.read_csv(os.path.join(outputPath, outputFilename), index_col=False)

In [29]:
pd.set_option('display.max_rows', None)
df.head(5000)

designIndex         design  iter   pos1x   pos1y    pos2x    pos2y  \
0               0  sky130hs/jpeg     0     0.0  1008.0    50.40  1058.40   
1               0  sky130hs/jpeg     0     0.0     0.0    50.40    50.40   
2               0  sky130hs/jpeg     0     0.0  1108.8    50.40  1117.76   
3               0  sky130hs/jpeg     0     0.0   907.2    50.40   957.60   
4               0  sky130hs/jpeg     0     0.0   806.4    50.40   856.80   
5               0  sky130hs/jpeg     0     0.0   100.8    50.40   151.20   
6               0  sky130hs/jpeg     0     0.0   201.6    50.40   252.00   
7               0  sky130hs/jpeg     0   100.8   201.6   151.20   252.00   
8               0  sky130hs/jpeg     0   100.8  1108.8   151.20  1117.76   
9               0  sky130hs/jpeg     0   100.8   907.2   151.20   957.60   
10              0  sky130hs/jpeg     0   100.8  1008.0   151.20  1058.40   
11              0  sky130hs/jpeg     0     0.0   302.4    50.40   352.80   
12              0  sky130hs/jpeg     0   100.8     0.0   151.20    50.40   
13              0  sky130hs/jpeg     0   100.8   100.8   151.20   151.20   
14              0  sky130hs/jpeg     0     0.0   705.6    50.40   756.00   
15              0  sky130hs/jpeg     0   201.6     0.0   252.00    50.40   
16              0  sky130hs/jpeg     0   100.8   504.0   151.20   554.40   
17              0  sky130hs/jpeg     0     0.0   403.2    50.40   453.60   
18              0  sky130hs/jpeg     0   100.8   302.4   151.20   352.80   
19              0  sky130hs/jpeg     0     0.0   504.0    50.40   554.40   
20              0  sky130hs/jpeg     0   201.6  1108.8   252.00  1117.76   
21              0  sky130hs/jpeg     0   201.6   100.8   252.00   151.20   
22              0  sky130hs/jpeg     0   100.8   806.4   151.20   856.80   
23              0  sky130hs/jpeg     0   201.6   201.6   252.00   252.00   
24              0  sky130hs/jpeg     0   201.6  1008.0   252.00  1058.40   
25              0  sky130hs/jpeg     0   201.6   907.2   252.00   957.60   
26              0  sky130hs/jpeg     0   100.8   403.2   151.20   453.60   
27              0  sky130hs/jpeg     0   302.4     0.0   352.80    50.40   
28              0  sky130hs/jpeg     0   302.4   100.8   352.80   151.20   
29              0  sky130hs/jpeg     0   201.6   806.4   252.00   856.80   
30              0  sky130hs/jpeg     0   201.6   604.8   252.00   655.20   
31              0  sky130hs/jpeg     0   302.4   403.2   352.80   453.60   
32              0  sky130hs/jpeg     0   302.4  1108.8   352.80  1117.76   
33              0  sky130hs/jpeg     0   201.6   504.0   252.00   554.40   
34              0  sky130hs/jpeg     0   201.6   302.4   252.00   352.80   
35              0  sky130hs/jpeg     0   302.4   302.4   352.80   352.80   
36              0  sky130hs/jpeg     0   302.4   504.0   352.80   554.40   
37              0  sky130hs/jpeg     0   302.4  1008.0   352.80  1058.40   
38              0  sky130hs/jpeg     0   201.6   403.2   252.00   453.60   
39              0  sky130hs/jpeg     0   302.4   907.2   352.80   957.60   
40              0  sky130hs/jpeg     0   302.4   604.8   352.80   655.20   
41              0  sky130hs/jpeg     0   403.2   100.8   453.60   151.20   
42              0  sky130hs/jpeg     0   403.2     0.0   453.60    50.40   
43              0  sky130hs/jpeg     0   403.2   201.6   453.60   252.00   
44              0  sky130hs/jpeg     0   403.2  1108.8   453.60  1117.76   
45              0  sky130hs/jpeg     0     0.0   604.8    50.40   655.20   
46              0  sky130hs/jpeg     0   403.2   504.0   453.60   554.40   
47              0  sky130hs/jpeg     0   403.2  1008.0   453.60  1058.40   
48              0  sky130hs/jpeg     0   302.4   705.6   352.80   756.00   
49              0  sky130hs/jpeg     0   504.0     0.0   554.40    50.40   
50              0  sky130hs/jpeg     0   302.4   201.6   352.80   252.00   
51              0  sky130hs/jpeg     0   302.4   806.4

In [30]:
# get accumulative DRC for each iteration
# DRC = sum(curr_drc)
data = []
designIndexList = list(set(df['designIndex']))
for i in designIndexList:
    iterList = list(set(df[df['designIndex']==i]['iter']))
    for iter in iterList:
        currSum = df[df['designIndex']==i][df['iter']==iter]['curr_drc'].values.sum()
        preSum = df[df['designIndex']==i][df['iter']==iter]['prev_drc'].values.sum()
        data.append([i, iter, preSum, currSum, currSum - preSum])
data

/tmp/ipykernel_85358/2687475815.py:8: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  currSum = df[df['designIndex']==i][df['iter']==iter]['curr_drc'].values.sum()
/tmp/ipykernel_85358/2687475815.py:9: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  preSum = df[df['designIndex']==i][df['iter']==iter]['prev_drc'].values.sum()
/tmp/ipykernel_85358/2687475815.py:8: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  currSum = df[df['designIndex']==i][df['iter']==iter]['curr_drc'].values.sum()
/tmp/ipykernel_85358/2687475815.py:9: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  preSum = df[df['designIndex']==i][df['iter']==iter]['prev_drc'].values.sum()
/tmp/ipykernel_85358/2687475815.py:8: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  currSum = df[df['designIndex']==i][df['iter']==iter]['curr_drc'].values.sum()
/tmp/ipykernel_85358/2687475815.

[[0, 0, 4439, 23530, 19091],
 [0, 1, 20310, 9980, -10330],
 [0, 2, 9795, 9463, -332],
 [0, 3, 9015, 1041, -7974],
 [0, 4, 697, 302, -395],
 [0, 5, 255, 56, -199],
 [0, 6, 52, 58, 6],
 [0, 7, 45, 63, 18],
 [0, 8, 37, 112, 75],
 [0, 9, 34, 48, 14],
 [0, 10, 27, 8, -19],
 [0, 11, 8, 3, -5],
 [0, 12, 3, 1, -2],
 [0, 13, 1, 1, 0],
 [0, 14, 1, 1, 0],
 [0, 15, 1, 1, 0],
 [0, 16, 1, 1, 0],
 [0, 17, 1, 1, 0],
 [0, 18, 1, 1, 0],
 [0, 19, 1, 1, 0],
 [0, 20, 1, 1, 0],
 [0, 21, 1, 1, 0],
 [0, 22, 1, 1, 0],
 [0, 23, 1, 1, 0],
 [0, 24, 1, 1, 0],
 [0, 25, 1, 1, 0],
 [0, 26, 1, 1, 0],
 [0, 27, 1, 1, 0],
 [0, 28, 1, 1, 0],
 [0, 29, 1, 1, 0],
 [0, 30, 1, 1, 0],
 [0, 31, 1, 1, 0],
 [0, 32, 1, 1, 0],
 [0, 33, 1, 1, 0],
 [0, 34, 1, 1, 0],
 [0, 35, 1, 1, 0],
 [0, 36, 1, 1, 0],
 [0, 37, 1, 1, 0],
 [0, 38, 1, 1, 0],
 [0, 39, 1, 1, 0],
 [0, 40, 1, 1, 0],
 [0, 41, 1, 1, 0],
 [0, 42, 1, 1, 0],
 [0, 43, 1, 1, 0],
 [0, 44, 1, 1, 0],
 [0, 45, 1, 1, 0],
 [0, 46, 1, 1, 0],
 [0, 47, 1, 1, 0],
 [0, 48, 1, 1, 0],
 [0, 49

In [31]:
# save summary data
dfsummary = pd.DataFrame(data, columns=['designIndex', 'iter', 'curr_drc', 'prev_drc', 'delta_drc'])
dfsummary

designIndex  iter  curr_drc  prev_drc  delta_drc
0              0     0      4439     23530      19091
1              0     1     20310      9980     -10330
2              0     2      9795      9463       -332
3              0     3      9015      1041      -7974
4              0     4       697       302       -395
5              0     5       255        56       -199
6              0     6        52        58          6
7              0     7        45        63         18
8              0     8        37       112         75
9              0     9        34        48         14
10             0    10        27         8        -19
11             0    11         8         3         -5
12             0    12         3         1         -2
13             0    13         1         1          0
14             0    14         1         1          0
15             0    15         1         1          0
16             0    16         1         1          0
17             0    17         1         1          0
18             0    18         1         1          0
19             0    19         1         1          0
20             0    20         1         1          0
21             0    21         1         1          0
22             0    22         1         1          0
23             0    23         1         1          0
24             0    24         1         1          0
25             0    25         1         1          0
26             0    26         1         1          0
27             0    27         1         1          0
28             0    28         1         1          0
29             0    29         1         1          0
30             0    30         1         1          0
31             0    31         1         1          0
32             0    32         1         1          0
33             0    33         1         1          0
34             0    34         1         1          0
35             0    35         1         1          0
36             0    36         1         1          0
37             0    37         1         1          0
38             0    38         1         1          0
39             0    39         1         1          0
40             0    40         1         1          0
41             0    41         1         1          0
42             0    42         1         1          0
43             0    43         1         1          0
44             0    44         1         1          0
45             0    45         1         1          0
46             0    46         1         1          0
47             0    47         1         1          0
48             0    48         1         1          0
49             0    49         1         1          0
50             0    50         1         1          0
51             0    51         1         1          0
52             0    52         1         1          0
53             0    53         1         1          0
54             0    54         1         1          0
55             0    55         1         1          0
56             0    56         1         1          0
57             0    57         1         1          0
58             0    58         1         1          0
59             0    59         1         1          0
60             0    60         1         1          0
61             0    61         1         1          0
62             0    62         1         1          0
63             0    63         1         1          0
64             0    64         1         1          0
65             1     0      3077     20335      17258
66             1     1     18494     13402      -5092
67             1     2     13126     12195       -931
68             1     3     11961      2996      -8965
69             1     4      2399      1661       -738
70             1     5      1229      1248         19
71             1     6       921       708       -213
72             1     7       526       469        -57
73       

In [35]:
# save summary data continue
summaryPath = "../data/dataset"
summaryFilename = "workerDataSummary.csv"
if not os.path.exists(summaryPath):
    print(f"Output path {summaryPath} doesn't exist!")
else:
    dfsummary.to_csv(os.path.join(summaryPath, summaryFilename), index=False)

In [36]:
# read summary data
summaryPath = "../data/dataset"
summaryFilename = "workerDataSummary.csv"
df = pd.read_csv(os.path.join(summaryPath, summaryFilename), index_col=False)

In [37]:
df.head()

designIndex  iter  curr_drc  prev_drc  delta_drc
0            0     0      4439     23530      19091
1            0     1     20310      9980     -10330
2            0     2      9795      9463       -332
3            0     3      9015      1041      -7974
4            0     4       697       302       -395

In [38]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 480 entries, 0 to 479
Data columns (total 5 columns):
 #   Column       Non-Null Count  Dtype
---  ------       --------------  -----
 0   designIndex  480 non-null    int64
 1   iter         480 non-null    int64
 2   curr_drc     480 non-null    int64
 3   prev_drc     480 non-null    int64
 4   delta_drc    480 non-null    int64
dtypes: int64(5)
memory usage: 18.9 KB


In [39]:
df.describe()

designIndex        iter       curr_drc       prev_drc      delta_drc
count   480.000000  480.000000     480.000000     480.000000     480.000000
mean     13.172917   12.150000    5397.041667    5245.739583    -151.302083
std      10.620090   13.366615   19954.525240   21312.172227   18269.421559
min       0.000000    0.000000       1.000000       0.000000 -221311.000000
25%       2.000000    3.000000       7.000000       3.000000    -199.000000
50%      12.000000    7.000000      85.000000      86.000000      -0.500000
75%      20.000000   18.000000    1710.250000    1814.750000      22.000000
max      38.000000   64.000000  307386.000000  351868.000000  231508.000000

## get data with default settings

In [2]:
def parseDefaultOneLine(line, shapeCost=8, markerCost=32) -> list:
    """Parse 1 line of iteration setting"""
    # remove delimiters
    tmp = re.split(r'[\{\}\,]+', line)
    iteData = []
    # get size, offset, and mazeEndIter
    iteData.append(int(re.sub(r'\s+', '', tmp[1])))
    iteData.append(int(re.sub(r'\s+', '', tmp[2])))
    iteData.append(int(re.sub(r'\s+', '', tmp[3])))
    # get 1st cost
    compo = re.split(r'[\s\*]+', tmp[4])
    if len(compo) == 2: # no coefficient before shapeCost
        iteData.append(shapeCost)
    else:               # shapeCost with coefficient
        iteData.append(int(compo[1]) * shapeCost)
    # get 2nd cost
    compo = re.split(r'[\s\*]+', tmp[5])
    if len(compo) == 2: # no coefficient before shapeCost or markerCost
        if compo[1] == 'shapeCost':
            iteData.append(shapeCost)
        elif compo[1] == '0':
            iteData.append(0)
        else:
            iteData.append(markerCost)
    else:               # cost with coefficient
        iteData.append(int(compo[1]) * markerCost)
    # get 3rd cost
    compo = re.split(r'[\s\*]+', tmp[6])
    if len(compo) == 2: # no coefficient before shapeCost
        iteData.append(shapeCost)
    else:               # shapeCost with coefficient
        iteData.append(int(compo[1]) * shapeCost)
    # get decay
    iteData.append(float(re.sub(r'\s+', '', tmp[7])))
    # get mode
    mode = re.sub(r'[\s\:]+', '', tmp[8])
    if mode[-7:] == 'ModeALL':
        iteData.append('ALL')
    elif mode[-7:] == 'ModeDRC':
        iteData.append('DRC')
    else:
        iteData.append('NEARDRC')
    # get followGuide
    followGuide = re.sub(r'\s+', '', tmp[9])
    if followGuide == 'false':
        iteData.append(False)
    else:
        iteData.append(True)
        
    return iteData

In [3]:
# parse default strategy
def parseDefaultStrategy(inPath, outPath, shapeCost=8, markerCost=32) -> list:
    """Parse default strategy, save result to file, and return parsing status.
    
    Inputs:
    inPath: input FlexDR.cpp file path
    outPath: output result file path
    shapeCost: default shapeCost
    markerCost: default markerCost
    
    Return:
    Return list of strategy data.
    """
    # check file exists
    inputPath = os.path.join(inPath, "FlexDR.cpp")
    if not os.path.exists(inputPath):
        print("FlexDR.cpp for default setting doesn't exist in {}!".format(inputPath))
        return None
    # open, read, and extract coefficients from input file
    data = [] # temp coeff data
    count = 1
    with open(inputPath, 'r') as f:
        line = f.readline()
        while count < 1030:
            count = count + 1
            # check strategy() function
            if line == "static std::vector<FlexDR::SearchRepairArgs> strategy()\n":
                print("Start parsing iteration data!")
                # skip prefix lines
                line = f.readline()
                line = f.readline()
                line = f.readline()
                line = f.readline()
                count = count + 3
                # parse iteration settings
                while line != "  };\n":
                    # parse data
                    tempData = parseDefaultOneLine(line, shapeCost=shapeCost, markerCost=markerCost)
                    data.append(tempData)
                    # read next line
                    line = f.readline()
                    count = count + 1
                print("End parsing iteration data!")
            else:
                line = f.readline()
    # check output path exists
    if not os.path.exists(outPath):
        print("Output path {} for default setting data doesn't exist!".format(outPath))
        return None
    # create and write to output file
    with open(os.path.join(outPath, "defaultStrategy.txt"), 'w') as f:
        for line in data:
            for element in line:
                f.write("{},".format(element))
            f.write("@")
    return data

In [4]:
inPath = "/home/jborg/Data/Research/DLPnR/DL-PnR/data/default"
outPath = "/home/jborg/Data/Research/DLPnR/DL-PnR/src"
data = parseDefaultStrategy(inPath, outPath)

Start parsing iteration data!
End parsing iteration data!


In [5]:
def parseJSONFile(filename) -> list:
    """parse JSON file and return an output vector
    
    Inputs: 
    filename: path to 5_3_route.json file
    
    Return:
    A output vector containing the number of violations for each iteration
    """
    # check file exists
    if not os.path.exists(filename):
        print(filename)
        print("JSON file {} doesn't exist!".format(filename))
        return None
    # read and parse lines
    data = []
    with open(filename, 'r') as f:
        while True:
            line = f.readline()
            tmp = re.split(r'[\"\,\s\:]+', line)
            if len(tmp) > 2 and tmp[1] == 'detailedroute__route__drc_errors__iter':
                data.append(int(tmp[3]))
            if line == "}":
                break
    # return result
    return data

In [6]:
# parse default log files
def parseDefaultLogFiles(inPath, outPath) -> int:
    """Parse log files in the whole directory
    
    Inputs:
    inPath: log file directory
    outPath: output file path
    
    Return:
    Return list of output data.
    """
    # check path exists
    if not os.path.exists(inPath):
        print("Default log file path {} doesn't exist!".format(inPath))
        return None
    # check 5_3_route.json file exists and get outputs
    data = []
    for root, dirs, files in os.walk(inPath):
        for file in files:
            if file == "5_3_route.json":
                # parse json file for outputs
                data.append(parseJSONFile(os.path.join(root, file)))
                print("Data of {}: {}".format(os.path.join(root, file), parseJSONFile(os.path.join(root, file))))
    # check output path exists
    if not os.path.exists(outPath):
        print("Output path {} for default log data doesn't exist!".format(outPath))
        return None
    # create and write to output file
    with open(os.path.join(outPath, "defaultOutputs.txt"), 'w') as f:
        for line in data:
            for element in line:
                f.write("{},".format(element))
            f.write("\n")
            
    return data

In [7]:
data = parseDefaultLogFiles("/home/jborg/Data/Research/DLPnR/DL-PnR/data/default", 
                     "/home/jborg/Data/Research/DLPnR/DL-PnR/src")
data

Data of /home/jborg/Data/Research/DLPnR/DL-PnR/data/default/logs/gf180/riscv32i/base/5_3_route.json: [10178, 569, 499, 1, 0]
Data of /home/jborg/Data/Research/DLPnR/DL-PnR/data/default/logs/gf180/uart-blocks/base/5_3_route.json: [226, 18, 9, 0]
Data of /home/jborg/Data/Research/DLPnR/DL-PnR/data/default/logs/gf180/aes/base/5_3_route.json: [24561, 1453, 1030, 2, 0]
Data of /home/jborg/Data/Research/DLPnR/DL-PnR/data/default/logs/gf180/ibex/base/5_3_route.json: [16946, 864, 610, 8, 0]
Data of /home/jborg/Data/Research/DLPnR/DL-PnR/data/default/logs/gf180/jpeg/base/5_3_route.json: [20369, 983, 530, 0]
Data of /home/jborg/Data/Research/DLPnR/DL-PnR/data/default/logs/gf180/uart-blocks_uart_rx/base/5_3_route.json: [205, 10, 7, 0]
Data of /home/jborg/Data/Research/DLPnR/DL-PnR/data/default/logs/asap7/mock-array_Element/base/5_3_route.json: [155, 37, 40, 0]
Data of /home/jborg/Data/Research/DLPnR/DL-PnR/data/default/logs/asap7/mock-array/base/5_3_route.json: [1103, 302, 80, 0]
Data of /home/jb

[[10178, 569, 499, 1, 0],
 [226, 18, 9, 0],
 [24561, 1453, 1030, 2, 0],
 [16946, 864, 610, 8, 0],
 [20369, 983, 530, 0],
 [205, 10, 7, 0],
 [155, 37, 40, 0],
 [1103, 302, 80, 0],
 [32846, 1962, 1482, 1, 0],
 [6981, 684, 613, 3, 0],
 [88718, 11103, 7910, 350, 43, 4, 0],
 [12295, 1090, 911, 18, 0],
 [232, 16, 12, 1, 0],
 [55009,
  47472,
  51514,
  7698,
  953,
  179,
  106,
  10,
  10,
  11,
  7,
  6,
  5,
  5,
  4,
  4,
  4,
  1059,
  4,
  3,
  3,
  3,
  3,
  3,
  3,
  5,
  5,
  5,
  5,
  4,
  4,
  4,
  4,
  3,
  2,
  2,
  2,
  2,
  2,
  2,
  2,
  3,
  3,
  2,
  2,
  2,
  2,
  2,
  2,
  2,
  2,
  2,
  2,
  2,
  2,
  2,
  2,
  2,
  2,
  2,
  2,
  2,
  2,
  2,
  2],
 [177521,
  168983,
  142289,
  54869,
  10385,
  1540,
  790,
  505,
  72,
  60,
  32,
  24,
  19,
  18,
  13,
  11,
  10,
  11,
  5,
  6,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  0],
 [117297, 97675, 94141, 22881, 2915, 407, 69, 35, 24, 21, 10, 10, 7, 1, 1, 0],
 [325, 329, 157, 15, 0],
 [928, 1378, 1305, 285, 3, 0],
 [11941, 13

## get data with automatically generated settings

In [8]:
def parseOneLine(line) -> list:
    """Parse 1 line of iteration setting"""
    # remove delimiters
    tmp = re.split(r'[\{\}\,\t]+', line)
    iteData = []
    # get size, offset, mazeEndIter, 3 types of costs, and decay
    iteData.append(int(re.sub(r'\s+', '', tmp[1])))
    iteData.append(int(re.sub(r'\s+', '', tmp[2])))
    iteData.append(int(re.sub(r'\s+', '', tmp[3])))
    iteData.append(int(re.sub(r'\s+', '', tmp[4])))
    iteData.append(int(re.sub(r'\s+', '', tmp[5])))
    iteData.append(float(re.sub(r'\s+', '', tmp[6])))
    # get mode
    mode = re.sub(r'[\s\:]+', '', tmp[7])
    if mode[-3:] == 'ALL':
        iteData.append('ALL')
    elif mode[-7:] == 'NEARDRC':
        iteData.append('NEARDRC')
    else:
        iteData.append('DRC')
    # get followGuide
    followGuide = re.sub(r'\s+', '', tmp[8])
    if followGuide == 'false':
        iteData.append(False)
    else:
        iteData.append(True)
        
    return iteData

In [9]:
# line = "			{7,	0,	3,	7,	71,	0.745245,	RipUpMode::ALL,	true},"
# parseOneLine(line)

In [10]:
# parse default strategy
def parseStrategy(inPath) -> list:
    """Parse default strategy, save result to file, and return parsing status.
    
    Inputs:
    inPath: input FlexDR.cpp file path
    shapeCost: default shapeCost
    markerCost: default markerCost
    
    Return:
    Return list of strategy data.
    """
    # check file exists
    inputPath = os.path.join(inPath, "FlexDR.cpp")
    if not os.path.exists(inputPath):
        print("FlexDR.cpp for default setting doesn't exist in {}!".format(inputPath))
        return None
    # open, read, and extract coefficients from input file
    data = [] # temp coeff data
    count = 1
    with open(inputPath, 'r') as f:
        line = f.readline()
        while count < 1030:
            count = count + 1
            # check strategy() function
            if line == "static std::vector<FlexDR::SearchRepairArgs> strategy()\n":
                print("Start parsing iteration data!")
                # skip prefix lines
                line = f.readline()
                line = f.readline()
                line = f.readline()
                line = f.readline()
                count = count + 3
                # parse iteration settings
                while line != "  };\n":
                    # parse data
                    tempData = parseOneLine(line)
                    data.append(tempData)
                    # read next line
                    line = f.readline()
                    count = count + 1
                print("End parsing iteration data!")
            else:
                line = f.readline()

    return data

In [11]:
# parseStrategy("/home/jborg/Data/Research/DLPnR/DL-PnR/data/random/logs/asap7/aes")

In [12]:
def parseStrategyAndLog(inPath, outPath) -> int:
    """Parse artificially generated strategy, save result to file, and return parsing status.
    
    Inputs:
    inPath: input FlexDR.cpp file path
    outPath: output result file path
    
    Return:
    Return 0 for correct result. 1 for Error
    """
    # check input file exists
    if not os.path.exists(inPath):
        print("Log file path {} doesn't exist!".format(inPath))
        return 1
    # traverse design folders
    coeffData = []
    outData = []
    for Folder in os.listdir(inPath):
        for folder in os.listdir(os.path.join(inPath, Folder)):
            # check FlexDR.cpp and 5_3_route.json file exists
            currentDir = os.path.join(inPath, Folder, folder)
            print("\n\n")
            print(currentDir)
            cppFilename = os.path.join(currentDir, "FlexDR.cpp")
            jsonFilename = os.path.join(currentDir, "base/5_3_route.json")
            if os.path.exists(cppFilename) and os.path.exists(jsonFilename):
                print("\tGet data from {}".format(currentDir))
                # get iteration settings
                strategy = parseStrategy(currentDir)
                coeffData.append(strategy)
                print(coeffData)
                # get outputs
                out = parseJSONFile(jsonFilename)
                outData.append(out)
                print(out)
    # check output path exists
    if not os.path.exists(outPath):
        print("Output path {} doesn't exist!".format(outPath))
        return 1
    # create and write to output file
    with open(os.path.join(outPath, "strategy.txt"), 'w') as f:
        for strategy in coeffData:
            for line in strategy:
                for element in line:
                    f.write("{},".format(element))
                f.write("@")
            f.write("\n")
    with open(os.path.join(outPath, "outputs.txt"), 'w') as f:
        for line in outData:
            for element in line:
                f.write("{},".format(element))
            f.write("\n")
    return 0

In [13]:
inPath = "/home/jborg/Data/Research/DLPnR/DL-PnR/data/random/logs"
outPath = "/home/jborg/Data/Research/DLPnR/DL-PnR/src"
parseStrategyAndLog(inPath, outPath)




/home/jborg/Data/Research/DLPnR/DL-PnR/data/random/logs/gf180/riscv32i
	Get data from /home/jborg/Data/Research/DLPnR/DL-PnR/data/random/logs/gf180/riscv32i
Start parsing iteration data!
End parsing iteration data!
[[[7, 0, 63, 7, 91, 0.897397, 'ALL', True], [7, -1, 9, 12, 8, 0.563063, 'ALL', True], [7, -2, 3, 4, 69, 0.951451, 'ALL', True], [7, -3, 51, 6, 94, 0.611111, 'DRC', False], [7, -4, 51, 4, 4, 0.876376, 'DRC', False], [7, -5, 20, 8, 73, 0.654154, 'DRC', False], [7, -6, 3, 13, 75, 0.95045, 'DRC', False], [7, 0, 5, 11, 54, 0.957958, 'DRC', False], [7, -1, 56, 2, 18, 0.718719, 'DRC', False], [7, -2, 41, 12, 25, 0.624124, 'DRC', False], [7, -3, 20, 15, 67, 0.598098, 'DRC', False], [7, -4, 63, 1, 3, 0.522022, 'DRC', False], [7, -5, 20, 2, 76, 0.715215, 'DRC', False], [7, -6, 32, 6, 39, 0.52953, 'DRC', False], [7, 0, 11, 15, 67, 0.525526, 'DRC', False], [7, -1, 19, 4, 64, 0.808308, 'DRC', False], [7, -2, 33, 5, 92, 0.556557, 'DRC', False], [7, -3, 24, 5, 52, 0.657157, 'DRC', False

[32773, 4595, 3485, 279, 31, 0]



/home/jborg/Data/Research/DLPnR/DL-PnR/data/random/logs/nangate45/tinyRocket
	Get data from /home/jborg/Data/Research/DLPnR/DL-PnR/data/random/logs/nangate45/tinyRocket
Start parsing iteration data!
End parsing iteration data!
[[[7, 0, 63, 7, 91, 0.897397, 'ALL', True], [7, -1, 9, 12, 8, 0.563063, 'ALL', True], [7, -2, 3, 4, 69, 0.951451, 'ALL', True], [7, -3, 51, 6, 94, 0.611111, 'DRC', False], [7, -4, 51, 4, 4, 0.876376, 'DRC', False], [7, -5, 20, 8, 73, 0.654154, 'DRC', False], [7, -6, 3, 13, 75, 0.95045, 'DRC', False], [7, 0, 5, 11, 54, 0.957958, 'DRC', False], [7, -1, 56, 2, 18, 0.718719, 'DRC', False], [7, -2, 41, 12, 25, 0.624124, 'DRC', False], [7, -3, 20, 15, 67, 0.598098, 'DRC', False], [7, -4, 63, 1, 3, 0.522022, 'DRC', False], [7, -5, 20, 2, 76, 0.715215, 'DRC', False], [7, -6, 32, 6, 39, 0.52953, 'DRC', False], [7, 0, 11, 15, 67, 0.525526, 'DRC', False], [7, -1, 19, 4, 64, 0.808308, 'DRC', False], [7, -2, 33, 5, 92, 0.556557, 'DRC', False

0